All previous training was performed on the box-cox transformation of the target variable `UltimateIncurredClaimCost`. This trial will predict on the log instead.

In [1]:
import pandas as pd
import numpy as np

from sklearn.compose import ColumnTransformer, TransformedTargetRegressor
from sklearn.preprocessing import (
    FunctionTransformer,
    PowerTransformer,
    MinMaxScaler,
    OneHotEncoder,
    Binarizer,
    StandardScaler
)


from sklearn.pipeline import Pipeline
from sklearn.model_selection import cross_val_score, KFold, cross_val_predict
from sklearn.metrics import mean_squared_error, mean_absolute_error
from lightgbm import LGBMRegressor
from xgboost import XGBRegressor
from sklearn.decomposition import PCA


import mlflow
import mlflow.sklearn

from matplotlib import pyplot as plt
import seaborn as sns
import optuna

In [2]:
dataset_train = pd.read_csv('../data/processed/dataset_train.csv', index_col=0)
dataset_test = pd.read_csv('../data/processed/dataset_test.csv', index_col=0)

In [3]:
# column names
cols_event_embeddings = [f'event_feat_{i}' for i in range(768)]
cols_event_dummies = ['BACK STRAIN', 'CLEANING INSTRUMENTS', 'CLEANING LEFT SHOULDER SPLINTER', 'CUT WITH KNIFE', 'DEALING CARDS RIGHT TENDON SYNOVITIS', 'FELL', 'FELL FROM LADDER', 'FELL OFF LADDER', 'FRACTURED LEFT WRIST FRACTURE', 'GRINDING FOREIGN BODY', 'GRINDING STEEL BEAM INFECTION', 'HIT AIR HOSE', 'HIT ELBOW', 'HIT FLOOR SHEET', 'INJURY', 'INJURY LIFTING', 'INJURY LIFTING STRAIN', 'JAMMED RIGHT HAND PUNCTURE', 'KNIFE LACERATION', 'KNIFE SLIPPED', 'LACERATION', 'LEFT LEG SNAKE BITE', 'LIFTING', 'LIFTING BOXES', 'LIFTING PATIENT', 'LIFTING TYRES', 'LOWER BACK STRAIN', 'MOTOR VEHICLE COLLISION', 'PREPARING PIPES FOR PAINTING PUNCTURE', 'PULLING CABLES', 'REDBACK SPIDER BITE', 'SLIPPED AND FELL', 'SLIPPED ON FLOOR', 'SLIPPED ON ROLLER', 'SLIPPED ON STAIRS', 'SLIPPED ON WET FLOOR', 'SLIPPED USING LATHE', 'SORTING ALUMINIUM BARS STRAIN', 'SPRAINED RIGHT ANKLE FRACTURE', 'STRAIN', 'STRAIN LIFTING PARTS', 'STRAIN LIFTING STRAIN', 'STRUCK KNIFE LACERATED', 'STRUCK KNIFE LACERATION', 'STRUCK PALLET', 'STRUCK WITH KNIFE', 'USING AIR HOSE STRAIN', 'USING DRILL']
cols_body_parts_embeddings = [f'body_feat_{i}' for i in range(768)]

In [4]:
def train_cv(model, X, y, metric = 'rmse', kfold = 5):

    if metric != 'rmse':
        raise NotImplemented

    scores = cross_val_score(model, X, y, cv=kfold, scoring='neg_mean_squared_error')

    mse_scores = -scores
    rmse_scores = np.sqrt(mse_scores)

    return rmse_scores.mean(), rmse_scores.std()

In [5]:
log_transformer = Pipeline([
    ('log', FunctionTransformer(np.log, validate=False)),
    ('scaler', StandardScaler()) 
])

# gender to bool 
def gender_to_bool(gender_column):
    """
    - Fill missing values with 'M'
    - Replace 'U' with 'M'
    - Return a boolean-ish column: 1 for 'M', 0 otherwise
    """
    g = pd.Series(gender_column.squeeze(), dtype=str).fillna('M').replace('U', 'M')
    is_male = (g == 'M').astype(int)
    return is_male.values.reshape(-1, 1)

gender_transformer = FunctionTransformer(gender_to_bool, validate=False)

# hours worked per week -> to buckets -> to one_hot
def bucket_hours_worked(dtt_array):
    return pd.cut(
        dtt_array.squeeze(), 
        bins=[-np.inf, 37, 41, np.inf],
        labels=["<=37", "37-41", ">41"]
    ).astype(str).values.reshape(-1, 1)

hours_worked_bucketer = FunctionTransformer(bucket_hours_worked, validate=False)
hours_worked_encoder = OneHotEncoder(drop='first')
hours_worked_pipeline = Pipeline([
    ('bucketizer', hours_worked_bucketer),
    ('encoder', hours_worked_encoder)
])

# DaysToReport (DateReported - DateTimeOfAccident) -> to buckets -> to one_hot
def bucket_days_to_report(dtt_array):
    return pd.cut(
        dtt_array.squeeze(), 
        bins=[-np.inf, 80, 300, 500, np.inf],
        labels=["<=80", "80-300", "300-500", ">500"]
    ).astype(str).values.reshape(-1, 1)

days_to_report_bucketer = FunctionTransformer(bucket_days_to_report, validate=False)
days_to_report_encoder = OneHotEncoder(drop='first')
days_to_report_pipeline = Pipeline([
    ('bucketizer', days_to_report_bucketer),
    ('encoder', days_to_report_encoder)
])

# DaysWorkedPerWeek -> 1 if equals 5, 0 in any other case 
def days_worked_binarize(days_array):
    # Ensure we handle arrays or DataFrames by squeezing to 1D
    days = days_array.squeeze()
    binarized = (days == 5).astype(int)
    # Return as 2D array: (n_samples x 1)
    return binarized.values.reshape(-1, 1) if isinstance(days, pd.Series) else binarized.reshape(-1, 1)

days_worked_transformer = FunctionTransformer(days_worked_binarize, validate=False)

In [6]:
preprocessor = ColumnTransformer(
    transformers=[
        ('log_inc', log_transformer, ['InitialIncurredCalimsCost', 'WeeklyWages']),
        ('minmax_scaler', MinMaxScaler(), ['Age', 'YearAccident']),
        ('gender_bool', gender_transformer, ['Gender']),
        ('hww_bool_onehot', hours_worked_pipeline, ['HoursWorkedPerWeek']),
        ('dtt_bool_onehot', days_to_report_pipeline, ['DaysToReport']),
        ('has_dependent_bool', Binarizer(threshold=0), ['DependentChildren']),
        ('worked_five_days_bool', days_worked_transformer, ['DaysWorkedPerWeek']),
        ('onehot', OneHotEncoder(drop='first'), ['MaritalStatus', 'PartTimeFullTime']),
        ('pca_event_embeddings', PCA(n_components=250), cols_event_embeddings),
        ('passthrough_event_dummies', 'passthrough', cols_event_dummies),
        ('pca_body_parts_embeddings', PCA(n_components=80), cols_body_parts_embeddings),
        ('std_scaler', StandardScaler(), ['event_median_cost'])
    ],
    remainder='drop'
)

In [7]:
regressor_pipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('linear_model', LGBMRegressor(force_col_wise=True))
])

model = TransformedTargetRegressor(
    regressor=regressor_pipeline,
    transformer=FunctionTransformer(np.log1p, inverse_func=np.expm1, validate=False) # here's the change
)

In [8]:

scores = cross_val_score(
    model, 
    dataset_train, 
    dataset_train['UltimateIncurredClaimCost'], 
    cv=5, 
    scoring='neg_mean_squared_error'
)
mse_scores = -scores
rmse_scores = np.sqrt(mse_scores)

print(f"CV MSE:  {mse_scores.mean():.3f}  (+/- {mse_scores.std():.3f})")
print(f"CV RMSE: {rmse_scores.mean():.3f}  (+/- {rmse_scores.std():.3f})")

[LightGBM] [Info] Total Bins 85015
[LightGBM] [Info] Number of data points in the train set: 43199, number of used features: 395
[LightGBM] [Info] Start training from score 8.064355


/Users/alexis/Projects/202502 Actuarial Loss Prediction/.env/lib/python3.10/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(


[LightGBM] [Info] Total Bins 85024
[LightGBM] [Info] Number of data points in the train set: 43199, number of used features: 395
[LightGBM] [Info] Start training from score 8.067515


/Users/alexis/Projects/202502 Actuarial Loss Prediction/.env/lib/python3.10/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(


[LightGBM] [Info] Total Bins 85026
[LightGBM] [Info] Number of data points in the train set: 43199, number of used features: 395
[LightGBM] [Info] Start training from score 8.063679


/Users/alexis/Projects/202502 Actuarial Loss Prediction/.env/lib/python3.10/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(


[LightGBM] [Info] Total Bins 85029
[LightGBM] [Info] Number of data points in the train set: 43199, number of used features: 395
[LightGBM] [Info] Start training from score 8.066131


/Users/alexis/Projects/202502 Actuarial Loss Prediction/.env/lib/python3.10/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(


[LightGBM] [Info] Total Bins 85028
[LightGBM] [Info] Number of data points in the train set: 43200, number of used features: 395
[LightGBM] [Info] Start training from score 8.062133
CV MSE:  569802735.060  (+/- 51080152.463)
CV RMSE: 23844.840  (+/- 1107.398)


/Users/alexis/Projects/202502 Actuarial Loss Prediction/.env/lib/python3.10/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(


In [9]:
X_train = dataset_train.drop(columns=['UltimateIncurredClaimCost'])
y_train = dataset_train['UltimateIncurredClaimCost']

def run_experiment(
        experiment_name, 
        run_name, 
        regressor_object, 
        kfold=5, 
        save_model=True
    ):
    """
    Runs an ML experiment with cross-validation and logs metrics to MLflow,
    tracking overall and segmented performance for targets above and below 100,000.

    Parameters:
    - experiment_name (str): Name of the MLflow experiment.
    - run_name (str): Name of the MLflow run.
    - regressor_object: The regression model.
    - kfold (int): Number of folds for cross-validation.
    - save_model (bool): Whether to save the trained model in MLflow.

    Logs:
    - Overall CV MSE, RMSE, and MAE
    - MSE, RMSE, and MAE for y_true > 100,000
    - MSE, RMSE, and MAE for y_true ≤ 100,000
    """

    # Define pipeline with preprocessing and model
    regressor_pipeline = Pipeline([
        ('preprocessor', preprocessor),
        ('linear_model', regressor_object)
    ])

    model = TransformedTargetRegressor(
        regressor=regressor_pipeline,
        transformer=PowerTransformer(method='box-cox', standardize=False)
    )

    # Set MLflow experiment
    mlflow.set_experiment(experiment_name)

    with mlflow.start_run(run_name=run_name):
        # Log hyperparameters
        params = model.get_params(deep=True)
        for param_name, param_value in params.items():
            if isinstance(param_value, (str, int, float, bool, type(None))):
                mlflow.log_param(param_name, param_value)
            else:
                mlflow.log_param(param_name, str(param_value)[:5000])
        
        mlflow.log_param("n_features_in", X_train.shape[1])

        # Perform cross-validation with predictions
        y_pred = cross_val_predict(model, X_train, y_train, cv=kfold)

        # Compute overall errors
        overall_mse = mean_squared_error(y_train, y_pred)
        overall_rmse = np.sqrt(overall_mse)
        overall_mae = mean_absolute_error(y_train, y_pred)

        # Compute errors for high and low y_true
        high_mask = y_train > 100000

        high_mse = mean_squared_error(y_train[high_mask], y_pred[high_mask])
        high_rmse = np.sqrt(high_mse)
        high_mae = mean_absolute_error(y_train[high_mask], y_pred[high_mask])
        
        low_mse = mean_squared_error(y_train[~high_mask], y_pred[~high_mask])
        low_rmse = np.sqrt(low_mse)
        low_mae = mean_absolute_error(y_train[~high_mask], y_pred[~high_mask])
    
        print(f"RMSE Overall:  {overall_rmse:.3f} | MAE: {overall_mae:.3f}")
        print(f"RMSE for low y_true (<= 100k): {low_rmse:.3f} | MAE: {low_mae:.3f}")
        print(f"RMSE for high y_true (> 100k): {high_rmse:.3f} | MAE: {high_mae:.3f}")
        

        # Log overall metrics
        mlflow.log_metric("cv_mse", overall_mse)
        mlflow.log_metric("cv_rmse", overall_rmse)
        mlflow.log_metric("cv_mae", overall_mae)

        # Log segmented metrics
        mlflow.log_metric("cv_mse_high", high_mse)
        mlflow.log_metric("cv_rmse_high", high_rmse)
        mlflow.log_metric("cv_mae_high", high_mae)
        mlflow.log_metric("cv_mse_low", low_mse)
        mlflow.log_metric("cv_rmse_low", low_rmse)
        mlflow.log_metric("cv_mae_low", low_mae)

        # Fit final model on full dataset
        if save_model:
            model.fit(X_train, y_train)
            mlflow.sklearn.log_model(model, artifact_path="models")
    
    return overall_rmse


In [10]:

def objective(trial):
    """Objective function for Optuna to optimize XGBoost hyperparameters."""
    
    # Suggest hyperparameters to optimize
    params = {
        "num_leaves": trial.suggest_int("num_leaves", 20, 500),
        "max_depth": trial.suggest_int("max_depth", 3, 15),
        "learning_rate": trial.suggest_float("learning_rate", 0.1, 0.4, log=True),
        "n_estimators": trial.suggest_int("n_estimators", 100, 600, step=100),
        "min_child_weight": trial.suggest_int("min_child_weight", 1, 10),
        "subsample": trial.suggest_float("subsample", 0.5, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.5, 1.0),
        "lambda_l1": trial.suggest_float("lambda_l1", 0.0, 13.0),
        "lambda_l2": trial.suggest_float("lambda_l2", 0.0, 13.0),
        "boosting_type": "gbdt",
        "objective": "regression",
        "force_col_wise": True,
        "metric": "rmse",
    }

    rmse = run_experiment(
        'Optuna LightGBM',
        'LightGBM optimization on Log(UltimateIncurredClaimCost)',
        LGBMRegressor(**params),
        kfold=5,
        save_model=False
    )

    return rmse


In [11]:
study = optuna.create_study(direction="minimize")
study.optimize(objective, n_trials=35)

# Print the best result
print(f"Best trial: {study.best_trial.params}")


[I 2025-03-02 19:22:19,272] A new study created in memory with name: no-name-13e4c4fd-9d3a-40ac-941d-b2dc0d652dd2


[LightGBM] [Warning] lambda_l1 is set=0.43277545545087626, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.43277545545087626
[LightGBM] [Warning] lambda_l2 is set=11.433431860112103, reg_lambda=0.0 will be ignored. Current value: lambda_l2=11.433431860112103
[LightGBM] [Warning] lambda_l1 is set=0.43277545545087626, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.43277545545087626
[LightGBM] [Warning] lambda_l2 is set=11.433431860112103, reg_lambda=0.0 will be ignored. Current value: lambda_l2=11.433431860112103
[LightGBM] [Info] Total Bins 85015
[LightGBM] [Info] Number of data points in the train set: 43199, number of used features: 395
[LightGBM] [Info] Start training from score 5.909642
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive ga

/Users/alexis/Projects/202502 Actuarial Loss Prediction/.env/lib/python3.10/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(


[LightGBM] [Warning] lambda_l1 is set=0.43277545545087626, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.43277545545087626
[LightGBM] [Warning] lambda_l2 is set=11.433431860112103, reg_lambda=0.0 will be ignored. Current value: lambda_l2=11.433431860112103
[LightGBM] [Warning] lambda_l1 is set=0.43277545545087626, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.43277545545087626
[LightGBM] [Warning] lambda_l2 is set=11.433431860112103, reg_lambda=0.0 will be ignored. Current value: lambda_l2=11.433431860112103
[LightGBM] [Warning] lambda_l1 is set=0.43277545545087626, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.43277545545087626
[LightGBM] [Warning] lambda_l2 is set=11.433431860112103, reg_lambda=0.0 will be ignored. Current value: lambda_l2=11.433431860112103
[LightGBM] [Info] Total Bins 85024
[LightGBM] [Info] Number of data points in the train set: 43199, number of used features: 395
[LightGBM] [Info] Start training from score 5.914034
[LightGBM] 

/Users/alexis/Projects/202502 Actuarial Loss Prediction/.env/lib/python3.10/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(


...

[LightGBM] [Warning] lambda_l1 is set=0.9867816446774444, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.9867816446774444
[LightGBM] [Warning] lambda_l2 is set=8.463786108033023, reg_lambda=0.0 will be ignored. Current value: lambda_l2=8.463786108033023
[LightGBM] [Warning] lambda_l1 is set=0.9867816446774444, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.9867816446774444
[LightGBM] [Warning] lambda_l2 is set=8.463786108033023, reg_lambda=0.0 will be ignored. Current value: lambda_l2=8.463786108033023
[LightGBM] [Info] Total Bins 85029
[LightGBM] [Info] Number of data points in the train set: 43199, number of used features: 395
[LightGBM] [Info] Start training from score 5.959808
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best

/Users/alexis/Projects/202502 Actuarial Loss Prediction/.env/lib/python3.10/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(


[LightGBM] [Warning] lambda_l1 is set=0.9867816446774444, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.9867816446774444
[LightGBM] [Warning] lambda_l2 is set=8.463786108033023, reg_lambda=0.0 will be ignored. Current value: lambda_l2=8.463786108033023
[LightGBM] [Warning] lambda_l1 is set=0.9867816446774444, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.9867816446774444
[LightGBM] [Warning] lambda_l2 is set=8.463786108033023, reg_lambda=0.0 will be ignored. Current value: lambda_l2=8.463786108033023
[LightGBM] [Info] Total Bins 85028
[LightGBM] [Info] Number of data points in the train set: 43200, number of used features: 395
[LightGBM] [Info] Start training from score 5.940370
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best

/Users/alexis/Projects/202502 Actuarial Loss Prediction/.env/lib/python3.10/site-packages/sklearn/utils/validation.py:2739: UserWarning: X does not have valid feature names, but LGBMRegressor was fitted with feature names
  warnings.warn(
[I 2025-03-02 19:37:51,948] Trial 34 finished with value: 23950.09829262799 and parameters: {'num_leaves': 286, 'max_depth': 3, 'learning_rate': 0.23927907890245503, 'n_estimators': 100, 'min_child_weight': 6, 'subsample': 0.9060713240803953, 'colsample_bytree': 0.923849896286125, 'lambda_l1': 0.9867816446774444, 'lambda_l2': 8.463786108033023}. Best is trial 13 with value: 23897.187626683113.


[LightGBM] [Warning] lambda_l1 is set=0.9867816446774444, reg_alpha=0.0 will be ignored. Current value: lambda_l1=0.9867816446774444
[LightGBM] [Warning] lambda_l2 is set=8.463786108033023, reg_lambda=0.0 will be ignored. Current value: lambda_l2=8.463786108033023
RMSE Overall:  23950.098 | MAE: 5691.124
RMSE for low y_true (<= 100k): 9473.517 | MAE: 3325.941
RMSE for high y_true (> 100k): 163974.491 | MAE: 134318.306
Best trial: {'num_leaves': 106, 'max_depth': 3, 'learning_rate': 0.2848108212816855, 'n_estimators': 200, 'min_child_weight': 5, 'subsample': 0.9357648937673344, 'colsample_bytree': 0.7258722469184484, 'lambda_l1': 2.7767599683743263, 'lambda_l2': 7.567746651210365}


In [12]:
import optuna.visualization as vis

fig = vis.plot_optimization_history(study)
fig.show()


In [13]:
fig = vis.plot_param_importances(study)
fig.show()


In [ ]:
best_params = study.best_trial.params


regressor_pipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('linear_model', LGBMRegressor(**best_params))
])

model = TransformedTargetRegressor(
    regressor=regressor_pipeline,
    transformer=FunctionTransformer(np.log1p, inverse_func=np.expm1, validate=False) # here's the change
)

### XGBoost

In [20]:

def objective(trial):
    """Objective function for Optuna to optimize XGBoost hyperparameters."""
    
    # Suggest hyperparameters to optimize
    params = {
        "n_estimators": trial.suggest_int("n_estimators", 100, 1000, step=100),
        "max_depth": trial.suggest_int("max_depth", 2, 10),
        "learning_rate": trial.suggest_float("learning_rate", 0.01, 0.3, log=True),
        "min_child_weight": trial.suggest_int("min_child_weight", 1, 10),
        "subsample": trial.suggest_float("subsample", 0.5, 1.0),
        "colsample_bytree": trial.suggest_float("colsample_bytree", 0.5, 1.0),
        "reg_alpha": trial.suggest_float("reg_alpha", 0.0, 1.0),
        "reg_lambda": trial.suggest_float("reg_lambda", 0.0, 10.0),
        "gamma": trial.suggest_float("gamma", 0.0, 5.0),
    }

    rmse = run_experiment(
        'Optuna XGBoost',
        'XGBoost optimization - on Log of UltimateIncurredClaimCost',
        XGBRegressor(**params),
        kfold=5,
        save_model=False
    )

    return rmse


In [21]:
study_xgb = optuna.create_study(direction="minimize")
study_xgb.optimize(objective, n_trials=35)

# Print the best result
print(f"Best trial: {study_xgb.best_trial.params}")


[I 2025-03-02 20:02:33,759] A new study created in memory with name: no-name-7fc531c1-2df7-410b-8f2e-015558e1cb5c
[I 2025-03-02 20:02:53,823] Trial 0 finished with value: 24013.52109264384 and parameters: {'n_estimators': 700, 'max_depth': 8, 'learning_rate': 0.08097393278513144, 'min_child_weight': 2, 'subsample': 0.8562247610452776, 'colsample_bytree': 0.5743978699746811, 'reg_alpha': 0.5660395870750784, 'reg_lambda': 5.839643012137597, 'gamma': 1.041963720305303}. Best is trial 0 with value: 24013.52109264384.


RMSE Overall:  24013.521 | MAE: 5564.914
RMSE for low y_true (<= 100k): 9180.294 | MAE: 3161.824
RMSE for high y_true (> 100k): 165389.156 | MAE: 136253.601


[I 2025-03-02 20:03:11,892] Trial 1 finished with value: 23894.654023240546 and parameters: {'n_estimators': 600, 'max_depth': 3, 'learning_rate': 0.0545607974513588, 'min_child_weight': 4, 'subsample': 0.5997266818951921, 'colsample_bytree': 0.6200245970039228, 'reg_alpha': 0.5234410440583043, 'reg_lambda': 1.5719019228242648, 'gamma': 1.2846430894957357}. Best is trial 1 with value: 23894.654023240546.


RMSE Overall:  23894.654 | MAE: 5650.191
RMSE for low y_true (<= 100k): 9341.575 | MAE: 3284.943
RMSE for high y_true (> 100k): 163938.173 | MAE: 134280.841


[I 2025-03-02 20:03:19,679] Trial 2 finished with value: 24083.851770668534 and parameters: {'n_estimators': 200, 'max_depth': 3, 'learning_rate': 0.16225365738753686, 'min_child_weight': 1, 'subsample': 0.6715091542567694, 'colsample_bytree': 0.8566876247069521, 'reg_alpha': 0.9858854291063264, 'reg_lambda': 2.4777832294415614, 'gamma': 3.835949532663505}. Best is trial 1 with value: 23894.654023240546.


...

RMSE Overall:  23954.399 | MAE: 5656.538
RMSE for low y_true (<= 100k): 9281.444 | MAE: 3274.660
RMSE for high y_true (> 100k): 164605.442 | MAE: 135191.596


[I 2025-03-02 20:14:29,593] Trial 33 finished with value: 23901.80091575552 and parameters: {'n_estimators': 300, 'max_depth': 5, 'learning_rate': 0.04128026750917067, 'min_child_weight': 7, 'subsample': 0.7229352240743268, 'colsample_bytree': 0.6471512056840519, 'reg_alpha': 0.997613720227212, 'reg_lambda': 9.499244744529639, 'gamma': 0.3056608408283233}. Best is trial 26 with value: 23876.745382761994.


RMSE Overall:  23901.801 | MAE: 5594.231
RMSE for low y_true (<= 100k): 9238.167 | MAE: 3214.157
RMSE for high y_true (> 100k): 164314.118 | MAE: 135031.180


[I 2025-03-02 20:14:49,099] Trial 34 finished with value: 23931.152415190332 and parameters: {'n_estimators': 500, 'max_depth': 4, 'learning_rate': 0.03625338336894041, 'min_child_weight': 6, 'subsample': 0.5962015178126024, 'colsample_bytree': 0.5466067078968203, 'reg_alpha': 0.5312398566360711, 'reg_lambda': 8.213262925171396, 'gamma': 1.319258309749315}. Best is trial 26 with value: 23876.745382761994.


RMSE Overall:  23931.152 | MAE: 5617.001
RMSE for low y_true (<= 100k): 9268.045 | MAE: 3239.262
RMSE for high y_true (> 100k): 164459.163 | MAE: 134926.972
Best trial: {'n_estimators': 1000, 'max_depth': 4, 'learning_rate': 0.03463735262663482, 'min_child_weight': 6, 'subsample': 0.6505482542856182, 'colsample_bytree': 0.6439850382002905, 'reg_alpha': 0.8846660757196081, 'reg_lambda': 9.906891446537806, 'gamma': 0.8975397424137239}


In [22]:


fig = vis.plot_optimization_history(study_xgb)
fig.show()


In [23]:
fig = vis.plot_param_importances(study_xgb)
fig.show()


In [25]:
fig = vis.plot_slice(study_xgb)
fig.show()


### Train best LightGBM and best XGBoost and output predictions for test

In [26]:
# lightGBM
best_params = study.best_trial.params

regressor_pipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('linear_model', LGBMRegressor(**best_params))
])

model = TransformedTargetRegressor(
    regressor=regressor_pipeline,
    transformer=FunctionTransformer(np.log1p, inverse_func=np.expm1, validate=False) # here's the change
)

In [27]:
model.fit(X_train, y_train)

[LightGBM] [Warning] lambda_l1 is set=2.7767599683743263, reg_alpha=0.0 will be ignored. Current value: lambda_l1=2.7767599683743263
[LightGBM] [Warning] lambda_l2 is set=7.567746651210365, reg_lambda=0.0 will be ignored. Current value: lambda_l2=7.567746651210365
[LightGBM] [Warning] lambda_l1 is set=2.7767599683743263, reg_alpha=0.0 will be ignored. Current value: lambda_l1=2.7767599683743263
[LightGBM] [Warning] lambda_l2 is set=7.567746651210365, reg_lambda=0.0 will be ignored. Current value: lambda_l2=7.567746651210365
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.027076 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 85037
[LightGBM] [Info] Number of data points in the train set: 53999, number of used features: 395
[LightGBM] [Info] Start training from score 8.064763
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positiv

TransformedTargetRegressor(regressor=Pipeline(steps=[('preprocessor',
                                                      ColumnTransformer(transformers=[('log_inc',
                                                                                       Pipeline(steps=[('log',
                                                                                                        FunctionTransformer(func=<ufunc 'log'>)),
                                                                                                       ('scaler',
                                                                                                        StandardScaler())]),
                                                                                       ['InitialIncurredCalimsCost',
                                                                                        'WeeklyWages']),
                                                                                      ('minmax_scaler',
                                                                                       MinMaxScaler(),
                                                                                       ['Age',
                                                                                        'YearAccident']),
                                                                                      ('gender_bool',
                                                                                       FunctionTransformer(func=<fun...
                                                                                       ['event_median_cost'])])),
                                                     ('linear_model',
                                                      LGBMRegressor(colsample_bytree=0.7258722469184484,
                                                                    lambda_l1=2.7767599683743263,
                                                                    lambda_l2=7.567746651210365,
                                                                    learning_rate=0.2848108212816855,
                                                                    max_depth=3,
                                                                    min_child_weight=5,
                                                                    n_estimators=200,
                                                                    num_leaves=106,
                                                                    subsample=0.9357648937673344))]),
                           transformer=FunctionTransformer(func=<ufunc 'log1p'>,
                                                           inverse_func=<ufunc 'expm1'>))

In [28]:
y_test_pred = model.predict(dataset_test)
y_test_pred

[LightGBM] [Warning] lambda_l1 is set=2.7767599683743263, reg_alpha=0.0 will be ignored. Current value: lambda_l1=2.7767599683743263
[LightGBM] [Warning] lambda_l2 is set=7.567746651210365, reg_lambda=0.0 will be ignored. Current value: lambda_l2=7.567746651210365


/Users/alexis/Projects/202502 Actuarial Loss Prediction/.env/lib/python3.10/site-packages/sklearn/utils/validation.py:2739: UserWarning:

X does not have valid feature names, but LGBMRegressor was fitted with feature names



array([ 6752.83340441,  2586.85431844, 22547.83284088, ...,
        6585.69552794,  7010.17951367,   406.86264687], shape=(36000,))

In [29]:
submission_df = pd.DataFrame(zip(dataset_test.index, y_test_pred), columns=['ClaimNumber', 'UltimateIncurredClaimCost'])

print(submission_df.shape)
submission_df.head()

(36000, 2)


ClaimNumber  UltimateIncurredClaimCost
0   WC8145235                6752.833404
1   WC2005111                2586.854318
2   WC6899143               22547.832841
3   WC5502023                 456.162911
4   WC4785156                3134.128018

In [30]:
submission_df.to_csv('../data/output/submission_lgbm_on_log.csv', index=False)

In [35]:
# XGBoost
best_params = study_xgb.best_trial.params

regressor_pipeline = Pipeline([
    ('preprocessor', preprocessor),
    ('linear_model', XGBRegressor(**best_params))
])

model = TransformedTargetRegressor(
    regressor=regressor_pipeline,
    transformer=FunctionTransformer(np.log1p, inverse_func=np.expm1, validate=False) # here's the change
)

In [36]:
model.fit(X_train, y_train)

TransformedTargetRegressor(regressor=Pipeline(steps=[('preprocessor',
                                                      ColumnTransformer(transformers=[('log_inc',
                                                                                       Pipeline(steps=[('log',
                                                                                                        FunctionTransformer(func=<ufunc 'log'>)),
                                                                                                       ('scaler',
                                                                                                        StandardScaler())]),
                                                                                       ['InitialIncurredCalimsCost',
                                                                                        'WeeklyWages']),
                                                                                      ('minmax_scaler',
                                                                                       MinMaxScaler(),
                                                                                       ['Age',
                                                                                        'YearAccident']),
                                                                                      ('gender_bool',
                                                                                       FunctionTransformer(func=<fun...
                                                                   learning_rate=0.03463735262663482,
                                                                   max_bin=None,
                                                                   max_cat_threshold=None,
                                                                   max_cat_to_onehot=None,
                                                                   max_delta_step=None,
                                                                   max_depth=4,
                                                                   max_leaves=None,
                                                                   min_child_weight=6,
                                                                   missing=nan,
                                                                   monotone_constraints=None,
                                                                   multi_strategy=None,
                                                                   n_estimators=1000,
                                                                   n_jobs=None,
                                                                   num_parallel_tree=None,
                                                                   random_state=None, ...))]),
                           transformer=FunctionTransformer(func=<ufunc 'log1p'>,
                                                           inverse_func=<ufunc 'expm1'>))

In [37]:
y_test_pred = model.predict(dataset_test)
y_test_pred

array([ 6294.9546 ,  2672.6099 , 21258.408  , ...,  5585.009  ,
        7332.1455 ,   391.37875], shape=(36000,), dtype=float32)

In [38]:
submission_df = pd.DataFrame(zip(dataset_test.index, y_test_pred), columns=['ClaimNumber', 'UltimateIncurredClaimCost'])

print(submission_df.shape)
submission_df.head()

(36000, 2)


ClaimNumber  UltimateIncurredClaimCost
0   WC8145235                6294.954590
1   WC2005111                2672.609863
2   WC6899143               21258.408203
3   WC5502023                 348.934723
4   WC4785156                2853.677490

In [39]:
submission_df.to_csv('../data/output/submission_xgb_on_log.csv', index=False)